In [37]:
import sys
from pathlib import Path
import json

import pandas as pd
import numpy as np
import shapely.geometry as sg
import matplotlib

DIR = Path('..')
sys.path.append(str(DIR))

import gtfs_kit as gk

DATA_DIR = DIR/'data/'

%load_ext autoreload
%autoreload 2
%matplotlib inline

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [38]:
# List feed

path = DATA_DIR/'cairns_gtfs.zip'
gk.list_gtfs(path)

file_name  file_size
0  calendar_dates.txt        387
1          routes.txt       1478
2           trips.txt     143081
3           stops.txt      26183
4          agency.txt        199
5      stop_times.txt    2561019
6          shapes.txt     864694
7        calendar.txt        337

In [39]:
# Read and print feed

feed = gk.read_gtfs(path, dist_units='km')
print(feed)

* agency --------------------
	                                         agency_name  \
0  Department of Transport and Main Roads - Trans...   

                 agency_url     agency_timezone agency_lang  agency_phone  
0  http://www.sunbus.com.au  Australia/Brisbane          en  (07)40576411  
* calendar --------------------
	                           service_id  monday  tuesday  wednesday  thursday  \
0          CNS2014-CNS_MUL-Weekday-00       1        1          1         1   
1  CNS2014-CNS_MUL-Weekday-00-0000100       0        0          0         0   
2         CNS2014-CNS_MUL-Saturday-00       0        0          0         0   
3           CNS2014-CNS_MUL-Sunday-00       0        0          0         0   

   friday  saturday  sunday start_date  end_date  
0       1         0       0   20140526  20141226  
1       1         0       0   20140530  20141226  
2       0         1       0   20140531  20141227  
3       0         0       1   20140601  20141228  
* calendar_dates ---

In [40]:
feed.describe()

indicator  \
0                           agencies   
1                           timezone   
2                         start_date   
3                           end_date   
4                         num_routes   
5                          num_trips   
6                          num_stops   
7                         num_shapes   
8                        sample_date   
9   num_routes_active_on_sample_date   
10   num_trips_active_on_sample_date   
11   num_stops_active_on_sample_date   

                                                value  
0   [Department of Transport and Main Roads - Tran...  
1                                  Australia/Brisbane  
2                                            20140526  
3                                            20141228  
4                                                  22  
5                                                1339  
6                                                 416  
7                                                  54  
8                                            20140529  
9                                                  20  
10                                                622  
11                                                416

In [41]:
# Validate

feed.validate()

type                                  message                    table  \
0  warning                             Feed expired  calendar/calendar_dates   
1  warning  Repeated pair (trip_id, departure_time)               stop_times   

                                                rows  
0                                                 []  
1  [17710, 17722, 17730, 17732, 17736, 17739, 177...

In [42]:
# Compute trip stats

trip_stats = feed.compute_trip_stats()
trip_stats.head().T

703  \
trip_id           CNS2014-CNS_MUL-Weekday-00-4165878   
route_id                                     110-423   
route_short_name                                 110   
route_type                                         3   
direction_id                                       0   
shape_id                                     1100023   
num_stops                                         35   
start_time                                  05:50:00   
end_time                                    06:50:00   
start_stop_id                                 750337   
end_stop_id                                   750449   
is_loop                                            0   
duration                                           1   
distance                                     32.5071   
speed                                        32.5071   

                                                  0    \
trip_id           CNS2014-CNS_MUL-Saturday-00-4165937   
route_id                                      110-423   
route_short_name                                  110   
route_type                                          3   
direction_id                                        0   
shape_id                                      1100023   
num_stops                                          35   
start_time                                   06:16:00   
end_time                                     07:10:00   
start_stop_id                                  750337   
end_stop_id                                    750449   
is_loop                                             0   
duration                                          0.9   
distance                                      32.5071   
speed                                          36.119   

                                                 704  \
trip_id           CNS2014-CNS_MUL-Weekday-00-4165879   
route_id                                     110-423   
route_short_name                                 110   
route_type                                         3   
direction_id                                       0   
shape_id                                     1100023   
num_stops                                         35   
start_time                                  06:20:00   
end_time                                    07:20:00   
start_stop_id                                 750337   
end_stop_id                                   750449   
is_loop                                            0   
duration                                           1   
distance                                     32.5071   
speed                                        32.5071   

                                                 705  \
trip_id           CNS2014-CNS_MUL-Weekday-00-4165880   
route_id                                     110-423   
route_short_name                                 110   
route_type                                         3   
direction_id                                       0   
shape_id                                     1100023   
num_stops                                         35   
start_time                                  06:50:00   
end_time                                    07:50:00   
start_stop_id                                 750337   
end_stop_id                                   750449   
is_loop                                            0   
duration                                           1   
distance                                     32.5071   
speed                                        32.5071   

                                                 706  
trip_id           CNS2014-CNS_MUL-Weekday-00-4165881  
route_id                                     110-423  
route_short_name                                 110  
route_type                                         3  
direction_id                                       0  
shape_id                                     1100023  
num_stops                                         35  
start

In [43]:
# Add shape_dist_traveled column to stop times

feed = feed.append_dist_to_stop_times(trip_stats)
feed.stop_times.head().T

17709  \
trip_id              CNS2014-CNS_MUL-Saturday-00-4165937   
arrival_time                                    06:16:00   
departure_time                                  06:16:00   
stop_id                                           750337   
stop_sequence                                          1   
pickup_type                                            0   
drop_off_type                                          0   
shape_dist_traveled                                    0   

                                                   17710  \
trip_id              CNS2014-CNS_MUL-Saturday-00-4165937   
arrival_time                                    06:16:00   
departure_time                                  06:16:00   
stop_id                                           750000   
stop_sequence                                          2   
pickup_type                                            0   
drop_off_type                                          0   
shape_dist_traveled                              0.46864   

                                                   17711  \
trip_id              CNS2014-CNS_MUL-Saturday-00-4165937   
arrival_time                                    06:18:00   
departure_time                                  06:18:00   
stop_id                                           750001   
stop_sequence                                          3   
pickup_type                                            0   
drop_off_type                                          0   
shape_dist_traveled                              1.19038   

                                                   17712  \
trip_id              CNS2014-CNS_MUL-Saturday-00-4165937   
arrival_time                                    06:20:00   
departure_time                                  06:20:00   
stop_id                                           750002   
stop_sequence                                          4   
pickup_type                                            0   
drop_off_type                                          0   
shape_dist_traveled                              2.15478   

                                                   17713  
trip_id              CNS2014-CNS_MUL-Saturday-00-4165937  
arrival_time                                    06:21:00  
departure_time                                  06:21:00  
stop_id                                           750003  
stop_sequence                                          5  
pickup_type                                            0  
drop_off_type                                          0  
shape_dist_traveled                                2.619

In [44]:
# Choose study dates

week = feed.get_first_week()
dates = [week[4], week[6]]  # First Friday and Sunday
dates

['20140530', '20140601']

In [45]:
# Compute feed time series

fts = feed.compute_feed_time_series(trip_stats, dates, freq='6H')
fts

indicator            num_trip_ends  num_trip_starts  num_trips  \
datetime                                                         
2014-05-30 00:00:00           14.0             17.0       17.0   
2014-05-30 06:00:00          214.0            240.0      242.0   
2014-05-30 12:00:00          248.0            253.0      281.0   
2014-05-30 18:00:00          155.0            126.0      160.0   
2014-05-31 00:00:00            NaN              NaN        NaN   
2014-05-31 06:00:00            NaN              NaN        NaN   
2014-05-31 12:00:00            NaN              NaN        NaN   
2014-05-31 18:00:00            NaN              NaN        NaN   
2014-06-01 00:00:00            0.0              0.0        0.0   
2014-06-01 06:00:00           68.0             80.0       80.0   
2014-06-01 12:00:00          111.0            110.0      122.0   
2014-06-01 18:00:00           84.0             76.0       87.0   

indicator            service_distance  service_duration  service_speed  
datetime                                                                
2014-05-30 00:00:00        582.579000         12.450000      46.793494  
2014-05-30 06:00:00       4954.224929        173.800000      28.505322  
2014-05-30 12:00:00       5505.336088        193.216667      28.493070  
2014-05-30 18:00:00       3248.283810        103.550000      31.369230  
2014-05-31 00:00:00               NaN               NaN            NaN  
2014-05-31 06:00:00               NaN               NaN            NaN  
2014-05-31 12:00:00               NaN               NaN            NaN  
2014-05-31 18:00:00               NaN               NaN            NaN  
2014-06-01 00:00:00         26.198832          0.766667      34.172389  
2014-06-01 06:00:00       1794.087189         55.766667      32.171318  
2014-06-01 12:00:00       2615.694132         81.516667      32.087845  
2014-06-01 18:00:00       1954.866162         59.633333      32.781434

In [46]:
gk.downsample(fts, freq='12H')


indicator            num_trip_ends  num_trip_starts  num_trips  \
datetime                                                         
2014-05-30 00:00:00          228.0            257.0      256.0   
2014-05-30 12:00:00          403.0            379.0      408.0   
2014-05-31 00:00:00            NaN              NaN        NaN   
2014-05-31 12:00:00            NaN              NaN        NaN   
2014-06-01 00:00:00           68.0             80.0       80.0   
2014-06-01 12:00:00          195.0            186.0      198.0   

indicator            service_distance  service_duration  service_speed  
datetime                                                                
2014-05-30 00:00:00       5536.803929        186.250000      29.727806  
2014-05-30 12:00:00       8753.619898        296.766667      29.496641  
2014-05-31 00:00:00               NaN               NaN            NaN  
2014-05-31 12:00:00               NaN               NaN            NaN  
2014-06-01 00:00:00       1820.286021         56.533333      32.198456  
2014-06-01 12:00:00       4570.560294        141.150000      32.380873

In [47]:
# Compute feed stats for first week

feed_stats = feed.compute_feed_stats(trip_stats, week)
feed_stats

num_stops  num_routes  num_trips  num_trip_starts  num_trip_ends  \
0        416          20        622              622            617   
0        416          20        622              622            617   
0        416          20        622              622            617   
0        416          20        622              622            617   
0        416          22        636              636            617   
0        416          22        437              437            415   
0        416          14        266              266            263   

   service_distance  service_duration  service_speed  peak_num_trips  \
0      13774.027234        472.600000      29.145212              39   
0      13774.027234        472.600000      29.145212              39   
0      13774.027234        472.600000      29.145212              39   
0      13774.027234        472.600000      29.145212              39   
0      14290.423827        483.016667      29.585778              39   
0       9911.526097        310.400000      31.931463              23   
0       6390.846315        197.683333      32.328706              17   

  peak_start_time peak_end_time      date  
0        08:16:00      08:18:00  20140526  
0        08:16:00      08:18:00  20140527  
0        08:16:00      08:18:00  20140528  
0        08:16:00      08:18:00  20140529  
0        08:16:00      08:18:00  20140530  
0        17:28:00      17:37:00  20140531  
0        14:31:00      14:37:00  20140601

In [48]:
# Compute route time series

rts = feed.compute_route_time_series(trip_stats, dates, freq='12H')
rts

indicator           num_trip_ends                                           \
route_id                  110-423 110N-423 111-423 112-423 113-423 120-423   
datetime                                                                     
2014-05-30 00:00:00          19.0      9.0    18.0     4.0     3.0    11.0   
2014-05-30 12:00:00          39.0      0.0    39.0    11.0     3.0    21.0   
2014-05-31 00:00:00           NaN      NaN     NaN     NaN     NaN     NaN   
2014-05-31 12:00:00           NaN      NaN     NaN     NaN     NaN     NaN   
2014-06-01 00:00:00           7.0      NaN     8.0     3.0     NaN     4.0   
2014-06-01 12:00:00          24.0      NaN    24.0     5.0     NaN    12.0   

indicator                                             ... service_speed  \
route_id            120N-423 121-423 122-423 123-423  ...      131N-423   
datetime                                              ...                 
2014-05-30 00:00:00      0.0    13.0    13.0    21.0  ...      0.000000   
2014-05-30 12:00:00      2.0    21.0    20.0    38.0  ...     24.067374   
2014-05-31 00:00:00      NaN     NaN     NaN     NaN  ...           NaN   
2014-05-31 12:00:00      NaN     NaN     NaN     NaN  ...           NaN   
2014-06-01 00:00:00      NaN     4.0     3.0     5.0  ...      0.000000   
2014-06-01 12:00:00      NaN    10.0    11.0    16.0  ...     25.503394   

indicator                                                                   \
route_id               133-423    140-423   140N-423    141-423    142-423   
datetime                                                                     
2014-05-30 00:00:00  25.035081  25.634669  46.755126  20.802088  26.021598   
2014-05-30 12:00:00  26.439134  25.832253   0.000000  20.828188  26.417789   
2014-05-31 00:00:00        NaN        NaN        NaN        NaN        NaN   
2014-05-31 12:00:00        NaN        NaN        NaN        NaN        NaN   
2014-06-01 00:00:00  27.937311        NaN        NaN        NaN  28.218140   
2014-06-01 12:00:00  27.917299        NaN        NaN        NaN  28.163040   

indicator                                                        
route_id               143-423   143W-423    150-423   150E-423  
datetime                                                         
2014-05-30 00:00:00  24.366138   0.000000  31.565566   0.000000  
2014-05-30 12:00:00  24.307749  30.331218  31.547064  34.121380  
2014-05-31 00:00:00        NaN        NaN        NaN        NaN  
2014-05-31 12:00:00        NaN        NaN        NaN        NaN  
2014-06-01 00:00:00        NaN  29.759761        NaN  33.270085  
2014-06-01 12:00:00        NaN  29.717174        NaN  33.242294  

[6 rows x 132 columns]

In [49]:
# Slice time series

inds = ['service_distance', 'service_duration', 'service_speed']
rids = ['110-423', '110N-423']

rts.loc[:, (inds, rids)]

indicator           service_distance             service_duration            \
route_id                     110-423    110N-423          110-423  110N-423   
datetime                                                                      
2014-05-30 00:00:00       677.652816  399.508778        21.016667  7.916667   
2014-05-30 12:00:00      1216.570247    0.000000        36.333333  0.000000   
2014-05-31 00:00:00              NaN         NaN              NaN       NaN   
2014-05-31 12:00:00              NaN         NaN              NaN       NaN   
2014-06-01 00:00:00       279.005147         NaN         8.066667       NaN   
2014-06-01 12:00:00       732.594405         NaN        21.266667       NaN   

indicator           service_speed             
route_id                  110-423   110N-423  
datetime                                      
2014-05-30 00:00:00     32.243592  50.464267  
2014-05-30 12:00:00     33.483585   0.000000  
2014-05-31 00:00:00           NaN        NaN  
2014-05-31 12:00:00           NaN        NaN  
2014-06-01 00:00:00     34.587415        NaN  
2014-06-01 12:00:00     34.448013        NaN

In [50]:
# Slice again by cross-section

rts.xs(rids[0], axis="columns", level=1)

indicator            num_trip_ends  num_trip_starts  num_trips  \
datetime                                                         
2014-05-30 00:00:00           19.0             23.0       23.0   
2014-05-30 12:00:00           39.0             36.0       40.0   
2014-05-31 00:00:00            NaN              NaN        NaN   
2014-05-31 12:00:00            NaN              NaN        NaN   
2014-06-01 00:00:00            7.0              9.0        9.0   
2014-06-01 12:00:00           24.0             23.0       25.0   

indicator            service_distance  service_duration  service_speed  
datetime                                                                
2014-05-30 00:00:00        677.652816         21.016667      32.243592  
2014-05-30 12:00:00       1216.570247         36.333333      33.483585  
2014-05-31 00:00:00               NaN               NaN            NaN  
2014-05-31 12:00:00               NaN               NaN            NaN  
2014-06-01 00:00:00        279.005147          8.066667      34.587415  
2014-06-01 12:00:00        732.594405         21.266667      34.448013

In [51]:
# Compute trip locations for every hour

rng = pd.date_range('1/1/2000', periods=24, freq='H')
times = [t.strftime('%H:%M:%S') for t in rng]
loc = feed.locate_trips(dates[0], times)
loc.head()

trip_id      time  rel_dist route_id  \
0  CNS2014-CNS_MUL-Weekday-00-4165878  06:00:00  0.152945  110-423   
1  CNS2014-CNS_MUL-Weekday-00-4165879  07:00:00  0.720587  110-423   
2  CNS2014-CNS_MUL-Weekday-00-4165880  07:00:00  0.152945  110-423   
3  CNS2014-CNS_MUL-Weekday-00-4165881  08:00:00  0.720587  110-423   
4  CNS2014-CNS_MUL-Weekday-00-4165882  08:00:00  0.202283  110-423   

   direction_id shape_id            lon           lat  
0             0  1100023  358185.343160  8.146203e+06  
1             0  1100023  364975.430686  8.134931e+06  
2             0  1100023  358185.343160  8.146203e+06  
3             0  1100023  364975.430686  8.134931e+06  
4             0  1100023  358825.454562  8.145533e+06

In [52]:
# Build a route timetable

route_id = feed.routes['route_id'].iat[0]
feed.build_route_timetable(route_id, dates).T

0      \
route_id                                        110-423   
service_id                   CNS2014-CNS_MUL-Weekday-00   
trip_id              CNS2014-CNS_MUL-Weekday-00-4165878   
trip_headsign                  The Pier Cairns Terminus   
direction_id                                          0   
block_id                                            NaN   
shape_id                                        1100023   
arrival_time                                   05:50:00   
departure_time                                 05:50:00   
stop_id                                          750337   
stop_sequence                                         1   
pickup_type                                           0   
drop_off_type                                         0   
shape_dist_traveled                                   0   
date                                           20140530   

                                                  1      \
route_id                                        110-423   
service_id                   CNS2014-CNS_MUL-Weekday-00   
trip_id              CNS2014-CNS_MUL-Weekday-00-4165878   
trip_headsign                  The Pier Cairns Terminus   
direction_id                                          0   
block_id                                            NaN   
shape_id                                        1100023   
arrival_time                                   05:50:00   
departure_time                                 05:50:00   
stop_id                                          750000   
stop_sequence                                         2   
pickup_type                                           0   
drop_off_type                                         0   
shape_dist_traveled                             0.46864   
date                                           20140530   

                                                  2      \
route_id                                        110-423   
service_id                   CNS2014-CNS_MUL-Weekday-00   
trip_id              CNS2014-CNS_MUL-Weekday-00-4165878   
trip_headsign                  The Pier Cairns Terminus   
direction_id                                          0   
block_id                                            NaN   
shape_id                                        1100023   
arrival_time                                   05:52:00   
departure_time                                 05:52:00   
stop_id                                          750001   
stop_sequence                                         3   
pickup_type                                           0   
drop_off_type                                         0   
shape_dist_traveled                             1.19038   
date                                           20140530   

                                                  3      \
route_id                                        110-423   
service_id                   CNS2014-CNS_MUL-Weekday-00   
trip_id              CNS2014-CNS_MUL-Weekday-00-4165878   
trip_headsign                  The Pier Cairns Terminus   
direction_id                                          0   
block_id                                            NaN   
shape_id                                        1100023   
arrival_time                                   05:54:00   
departure_time                                 05:54:00   
stop_id                                          750002   
stop_sequence                                         4   
pickup_type                                           0   
drop_off_type                                         0   
shape_dist_traveled                             2.15478   
date                                           20140530   

                                                  4      \
route_id                                        110-423   
service_id                   CNS2014-CNS_MUL-Weekday-00   
trip_id              CNS2014-CNS_MUL-Weekday-00-4165878   
trip_headsign                  The

In [53]:
# Compute screen line counts

path = DATA_DIR/'cairns_screen_line.geojson'
with path.open() as src:
    line = json.load(src)
    line = sg.shape(line['features'][0]['geometry'])
print(line)

feed.compute_screen_line_counts(line, dates)

LINESTRING (145.7326126098633 -16.84915165200684, 145.7393932342529 -16.84999364745065)


date                             trip_id route_id route_short_name  \
0   20140530  CNS2014-CNS_MUL-Weekday-00-4166383  120-423              120   
1   20140530  CNS2014-CNS_MUL-Weekday-00-4166383  120-423              120   
2   20140530  CNS2014-CNS_MUL-Weekday-00-4166384  120-423              120   
3   20140530  CNS2014-CNS_MUL-Weekday-00-4166384  120-423              120   
34  20140530  CNS2014-CNS_MUL-Weekday-00-4166400  120-423              120   
..       ...                                 ...      ...              ...   
97  20140601   CNS2014-CNS_MUL-Sunday-00-4166456  120-423              120   
82  20140601   CNS2014-CNS_MUL-Sunday-00-4166449  120-423              120   
83  20140601   CNS2014-CNS_MUL-Sunday-00-4166449  120-423              120   
98  20140601   CNS2014-CNS_MUL-Sunday-00-4166457  120-423              120   
99  20140601   CNS2014-CNS_MUL-Sunday-00-4166457  120-423              120   

   crossing_time  orientation  
0       05:42:28           -1  
1       05:50:28            1  
2       06:42:28           -1  
3       06:50:28            1  
34      07:31:32           -1  
..           ...          ...  
97      20:55:28            1  
82      21:58:28           -1  
83      22:06:28            1  
98      22:47:32           -1  
99      22:55:28            1  

[100 rows x 6 columns]

In [55]:
# Map routes

rids = feed.routes.route_id.loc[2:4]
feed.map_routes(rids, include_stops=True)
